**<h3>Author: Matthias Bartolo Id: 0436103L</h3>**

### Package imports

In [1]:
# Suggested imports. You may add your own here.

%matplotlib inline

import collections
import random
import matplotlib.pyplot as plt
import nltk
import numpy as np
import torch

device = 'cuda' if torch.cuda.is_available() else 'cpu'

# Text compression assignment

It is said that you can measure the intelligence of an AI from the amount it can compress a text without information loss.
One way to think about this is that, the more a text is predictable, the more words we can leave out of it as we can guess the missing words.
On the other hand, the more intelligent an AI is, the more it will find texts to be predictable and so the more words it can leave out and guess.
This has led to a competition called the [Hutter Prize](http://prize.hutter1.net/) where the objective is to compress a given text as much as possible.
The record for compressing a 1GB text file extracted from a Wikipedia snapshot is about 115MB.
The main hurdle here is that the program used to decompress the file must be treated as part of the compressed file, meaning that the program itself must also be small.

In this assignment, you're going to be doing something similar using a smaller text file and using neural language models to guess missing words.

## 1) Data processing (10%)

You have a train/dev/test split corpus of text from Wikipedia consisting of single sentences.
Each sentence is on a separate line and each sentence has been tokenised for you such that tokens are space separated.
This means that you only need to split by space to get the tokens.
The text has all been lowercased as well.
The objective here is to be able to compress the text losslessly, meaning that it can be decompressed back to the original string:

$$\text{decompress}(\text{compress}(t)) = t$$

Do not do any further pre-processing on the text (such as stemming) as it may result in unrecoverable information loss.
The test set is what we will be compressing and will not be processed at all as it will be treated as a single big string by the compression/decompression algorithms.

Do the following tasks:

1.1) Load the train set and dev set text files into a list of sentences where each sentence is tokenised (by splitting by space).
Do not load the test set.

In [2]:
def load_into_sentences(filename):
    """Loads the file with the given filename into a list of sentences.
    
    Args:
        filename (str): The filename to load.
        
    Returns:
        list: A list of sentences, where each sentence is a list of words.
    """
    # Opening file and reading lines. Stripping each line of whitespace and newlines.
    with open(filename, encoding='utf-8') as f:
        sentences = f.readlines()
        # Splitting the line by spaces and stripping each word of whitespace and newlines.
        sentences = [sentence.split() for sentence in sentences]
    return sentences

In [3]:
dev_sentences = load_into_sentences('dev.txt')
train_sentences = load_into_sentences('train.txt')

<h4> What are the uses of the different txt files? </h4>
<ul>
    <li> <b>train.txt</b> is used to train the model </li>
    <li> <b>dev.txt</b> is used to validate the model </li>
    <li> <b>test.txt</b> is used to test the model </li>
</ul>

In [4]:
print('\033[1m' + 'Number of sentences in dev set:' + '\033[0m' + ' {}'.format(len(dev_sentences)))
print('\033[1m' + 'The dev set contains the following sentences:' + '\033[0m' + ' {}'.format(dev_sentences))
print('\033[1m' + 'Number of sentences in train set:' + '\033[0m' + ' {}'.format(len(train_sentences)))
print('\033[1m' + 'The train set contains the following sentences:' + '\033[0m' + ' {}'.format(train_sentences))

Number of sentences in dev set: 1712
The dev set contains the following sentences: [['jones', 'viewed', 'the', 'resolution', 'as', 'the', 'framework', ',', 'and', 'not', 'the', 'final', 'solution', ',', 'for', 'enabling', 'librarians', 'to', 'confront', 'issues', 'that', 'hampered', '``', 'human', 'freedom', "''", '.'], ['he', 'lives', 'in', 'ottawa', ',', 'where', 'he', 'composes', 'full-time', '.'], ['many', 'natural', 'gas', 'pipelines', 'span', 'the', 'country', "'s", 'territory', '.'], ['until', 'recently', ',', 'the', 'study', 'of', 'sign', 'language', 'and', 'sociolinguistics', 'has', 'existed', 'in', 'two', 'separate', 'domains', '.'], ['in', 'the', 'house', 'of', 'commons', 'she', 'sat', 'on', 'the', 'commons', 'reference', 'group', 'on', 'representation', 'and', 'inclusion', 'and', 'previously', 'sat', 'on', 'the', 'consolidation', 'bills', '(', 'joint', 'committee', ')', 'and', 'women', 'and', 'equalities', 'committee', '.'], ['he', 'won', 'a', 'number', 'of', 'significant',

1.2) Extract a vocabulary consisting of the tokens that occur at least 3 times in the train set and output the size of your vocabulary.
Also output the most frequent vocabulary token in the train set, which should be 'the'.
Include the edge token, unknown token, and pad token in the vocabulary.

In [5]:
# The following constants were created to store the respective token values:
EDGE_TOKEN = '<EDGE>'
UNKNOWN_TOKEN = '<UNK>'
PADDING_TOKEN = '<PAD>'

In [6]:
def extract_vocabulary(sentences):
    """Extracts the vocabulary from the given sentences, for tokens that occur at least 3 times.
    
    Args:
        sentences (list): A list of sentences, where each sentence is a list of words.
        
    Returns:
        vocabulary (set): The vocabulary, containing tokens that occur at least 3 times.
        size: The size of the vocabulary.
        most_freq_token: The most frequent token in the vocabulary.
    """
    # Adding the edge, unknown and pad tokens to the vocabulary
    vocabulary = [EDGE_TOKEN, UNKNOWN_TOKEN, PADDING_TOKEN]

    # Counting the number of times each token occurs in the sentences
    counter = collections.Counter([token for sentence in sentences for token in sentence])

    # Adding all tokens that occur at least 3 times to the vocabulary
    vocabulary += [token for token, count in counter.items() if count >= 3]

    # Sorting the vocabulary
    vocabulary.sort()

    # Creating a set of the vocabulary
    vocabulary = set(vocabulary)
    
    # Retrieving the most frequent token
    most_freq_token = max(counter, key=counter.get)
    return vocabulary, len(vocabulary), most_freq_token


In [7]:
train_vocab, train_vocab_size, train_most_freq_token = extract_vocabulary(train_sentences)

In [8]:
print('\033[1m' + 'Size of vocabulary in train set:' + '\033[0m' + ' {}'.format(train_vocab_size))
print('\033[1m' + 'Most frequent token in train set:' + '\033[0m' + ' {}'.format(train_most_freq_token))
print('\033[1m' + 'The vocabulary of the train set:' + '\033[0m' + ' {}'.format(train_vocab))

Size of vocabulary in train set: 7874
Most frequent token in train set: the
The vocabulary of the train set: {'discarded', 'fischer', 'attack', 'children', 'soldier', 'girlfriend', 'someone', 'shakespeare', 'dorsal', 'nodes', 'nationally', 'adventure', 'statement', 'possessed', 'arts', 'lennon', 'mobility', 'katz', 'pm', 'velocity', 'bioethics', 'picture', 'detroit', 'ella', 'shelter', 'debris', 'tanzania', 'nfl', 'originally', 'comprehensive', 'play', 'knew', 'extending', 'weekend', 'bristol', 'publicity', 'elite', 'dub', 'uss', 'can', 'by-election', 'price', 'costume', 'gameplay', 'commander', 'inspiration', 'seed', 'minnesota', 'colleagues', 'cox', 'woodson', 'adequate', 'stance', 'round', 'allied', 'emerging', 'shark', 'traffic', 'lie', 'luxury', 'confused', 'impossible', 'successor', 'argue', 'sentenced', 'pieces', 'traditions', 'alongside', 'commercially', 'measured', 'subscription', 'matter', 'obregón', 'planet', 'measure', 'dino', 'divorced', 'dependent', 'way', 'palm', 'comman

1.3) Process the loaded token sequences for the train set and dev set using the vocabulary created above in a way that is suitable for a language model, making use of edge tokens, unknown tokens, and pad tokens.
Do not do this for the test set as well.

In [9]:
# Creating a constant to set as the normalized length, assuming that the normalized length is the length of the longest sentence in the train set
NORMALIZED_LENGTH = max([len(sentence) for sentence in train_sentences])
print('\033[1m' + 'The maximum length of a sentence in the train set:' + '\033[0m' + ' {}'.format(NORMALIZED_LENGTH))

The maximum length of a sentence in the train set: 50


In [10]:
def match_tokens(token, vocabulary):
    """Matches the given token to the corresponding token in the vocabulary.
    
    Args:
        token (str): The token to process.
        vocabulary (set): The vocabulary to match the token to.
        
    Returns:
        str: The processed token.
    """
    # If the token is in the vocabulary, return it
    if token in vocabulary:
        return token
    # If the token is not in the vocabulary, return the unknown token
    else:
        return UNKNOWN_TOKEN

In [11]:
def process_sentences(sentences):
    """Processes the given sentences through the use of the respective functions.
    
    Args:
        sentences (list): A list of sentences, where each sentence is a list of words.
        
    Returns:
        list: A list of sentences, where each sentence is a list of words.
    """
    # Processing each sentence
    processed_sentences = []
    for sentence in sentences:
        # Processing each token in the sentence
        processed_sentence = [match_tokens(token, train_vocab) for token in sentence]
        
        # Adding the processed sentence to the list of processed sentences, with the edge tokens and padding tokens
        processed_sentences.append([EDGE_TOKEN] + processed_sentence + [PADDING_TOKEN]*(NORMALIZED_LENGTH-len(processed_sentence)))
        
    return processed_sentences

In [12]:
processed_dev_sentences = process_sentences(dev_sentences)
processed_train_sentences = process_sentences(train_sentences)

In [13]:
print('\033[1m' + 'The processed dev set contains the following sentences:' + '\033[0m')
for sentence in processed_dev_sentences:
    print(sentence)

The processed dev set contains the following sentences:
['<EDGE>', 'jones', 'viewed', 'the', 'resolution', 'as', 'the', 'framework', ',', 'and', 'not', 'the', 'final', 'solution', ',', 'for', '<UNK>', '<UNK>', 'to', '<UNK>', 'issues', 'that', '<UNK>', '``', 'human', 'freedom', "''", '.', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>']
['<EDGE>', 'he', 'lives', 'in', '<UNK>', ',', 'where', 'he', '<UNK>', 'full-time', '.', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>']
['<EDGE>', 'many', 'natural', 'gas', '<UNK>', '<UNK>', '

In [14]:
print('\033[1m' + 'The processed train set contains the following sentences:' + '\033[0m')
for sentence in processed_train_sentences:
    print(sentence)

The processed train set contains the following sentences:
['<EDGE>', 'dr.', '<UNK>', 'mcdonald', 'is', 'a', 'life', 'long', '<UNK>', 'resident', 'who', 'taught', 'and', 'rose', 'through', 'the', 'ranks', 'of', 'the', 'district', 'she', 'now', 'leads', '.', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>']
['<EDGE>', 'he', 'received', 'his', 'ba', 'in', 'chemistry', ',', '<UNK>', '<UNK>', '<UNK>', ',', 'from', '<UNK>', 'college', 'in', '1', '9', '8', '1', '.', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>', '<PAD>']
['<EDGE>', 'the', 'growth', 'of', 'twin', 'cities', 'international', 'air

1.4) Finally, load the test set text file as single string and keep it in a variable.

In [15]:
def load_into_string(filename):
    """Loads the file with the given filename into a string.
    
    Args:
        filename (str): The filename to load.
        
    Returns:
        str: The string loaded from the file.
    """
    # Opening file and reading lines. Stripping each line of whitespace and newlines.
    with open(filename, encoding='utf-8') as f:
        text = f.read()
    # Removing whitespace and newlines from each sentence
    text = text.strip()
    return text

In [16]:
test_set = load_into_string('test.txt')

In [17]:
print('\033[1m' + 'Length of test text:' + '\033[0m' + ' {}'.format(len(test_set)))
print('\033[1m' + 'The test set:' + '\033[0m' + ' {}'.format(test_set))

Length of test text: 218470
The test set: this coincidence enabled freemasons to wear the forget-me-not badge as a secret sign of membership .
3 4 . 6 % of all households were made up of individuals , and 1 5 . 7 % had someone living alone who was 6 5 years of age or older .
in 2 0 1 1 , she wrote to the federal health minister outlining the seriousness of the problem , which she said `` is a form of
in 2 0 0 8 , he sang `` l.u.v . ''
at the time , he was already committed to another nbc midseason replacement comedy , `` come to papa '' , but the series was quickly canceled , allowing his full commitment to `` the office '' .
at the 2 0 0 6 census , its population was 8 1 , in 1 9 families .
other musicians in the band during the later period were bassists percy jones ( of brand x ) and steve cook , saxophonists alan wakeman and ray warleigh , and violinist ric sanders .
corbett said he had `` a mastery of the english language '' .
ivan is out on nightly patrol of the boundary when an 

## 2) Evaluation tools (10%)

We're going to need a function that evaluates our language models as well as a way to test this function before we make the language model.
To test the evaluation function, you need to make a mock model which can be used exactly like a language model but that works with some simple rules.
This mock model will then be used to check the evaluation, compression, and decompression functions before we've developed the language model.

In this assignment, a language model function assumes the following signature:

* A parameter `x_indexes` being a tensor that gives the model's input token indexes of a batch of sentences, starting with the edge token.
    The tensor is of type `int64` with shape `(batch size, time steps)`.
* Returns a tensor of logits predicting which vocabulary token can be the next token after each token in `x_indexes`.
    The tensor is of type `float32` with shape `(batch size, time steps, vocab size)`.

Do the following tasks:

2.1) Develop a mock language model.
This language model will be a module that predicts the next token after every token using these rules:

* If the actual previous token (not the predicted one) was 'the' then predict that the current token is 'dog'.
* Otherwise, predict that the current token is 'the'.

Remember that it is logits that will be returned by the forward function, not probabilities.
**Give the token being predicted a logit of 2 and all other tokens a logit of 0.**
The name of this class should be `MockModel`.

Hints:

* Feel free to use `for` loops and `if` statements.
* Remember that `x_indexes` is a tensor of previous tokens.
    For example, if `x_indexes` is `[[1, 3]]`, this is saying that the first token to predict has a previous token being 1 and the second token to predict has a previous token being 3.

Some test code has been provided to check that your mock model is correct.
Fix the test code as instructed in the comments.


</br>
<h4> What is the difference between logits and probabilities? </h4>
<ul>
    <li> <b>Logits</b> are the raw predictions that a classification model generates, which are then passed to a normalization function. </li>
    <li> <b>Probabilities</b> are the normalized output of a classification model after it has been processed by a softmax function. </li>
</ul>

In [18]:
# Creating an index mapping for the vocabulary
index_mapping = {token: index for index, token in enumerate(train_vocab)}

In [19]:
def get_index(token, index_mapping):
    """Takes a token and returns the corresponding index.
    
    Args:
        token (str): The token to process.
        index_mapping (dict): A dictionary mapping tokens to indices.
        
    Returns:
        int: The index of the token.
    """
    
    return index_mapping.get(token, index_mapping[UNKNOWN_TOKEN])

In [20]:
class MockModel(torch.nn.Module):
    """A mock model that predicts the next token in a sequence.
    
    Model Rules:
    - If the previous token was 'the', predict 'dog'.
    - Otherwise predict 'the'.
    
    """
    def __init__(self, vocab_size, index_of_edge, index_of_the, index_of_dog):
        super().__init__()
        self.vocab_size = vocab_size
        self.index_of_edge = index_of_edge
        self.index_of_the = index_of_the
        self.index_of_dog = index_of_dog
        
    def forward(self, x_indexes):
        """Predicts the next token in the sequence.

        Args:
            x_indexes (torch.Tensor): A tensor that gives the model's input token indexes of a batch of sentences, starting with the edge token.
                                    The tensor is of type `int64` with shape `(batch size, time steps)`
        Returns:
            torch.Tensor: A tensor of logits predicting which vocabulary token can be the next token after each token in `x_indexes`.
                                    The tensor is of type `float32` with shape `(batch size, time steps, vocab size)`.
        """
        # Creating an empty list to store the logits
        logits = []

        # Iterating through the inputted tensor batch
        for batch in x_indexes:
            # Creating an empty list to store the logits for each token in the batch
            batch_logits = []

            # Iterating through the tokens in the batch
            for token in batch:
                # Respective if conditions for the rules of the model
                if token == self.index_of_the:  # If the current token is 'the', predict 'dog'
                    # Creating a tensor with the prediction for 'dog' (logit of 2.0)
                    next_token_logits = torch.full((self.vocab_size,), 0.0, dtype=torch.float32, device=device)
                    next_token_logits[self.index_of_dog] = 2.0
                else:  # Otherwise predicting 'the'
                    # Creating a tensor with the prediction for 'the' (logit of 2.0)
                    next_token_logits = torch.full((self.vocab_size,), 0.0, dtype=torch.float32, device=device)
                    next_token_logits[self.index_of_the] = 2.0
                
                # Appending the logits for the token to the list of logits for the batch
                batch_logits.append(next_token_logits)

            logits.append(torch.stack(batch_logits))

        return torch.stack(logits)

In [21]:
vocab_size = len(train_vocab) # You can change this to whatever code gives you the vocabulary size.
index_of_edge = get_index(EDGE_TOKEN, index_mapping) # You can change this to whatever code gives you the index of the edge token.
index_of_the = get_index('the', index_mapping) # You can change this to whatever code gives you the index of the token 'the'.
index_of_dog = get_index('dog', index_mapping) # You can change this to whatever code gives you the index of the token 'dog'.
mock_model = MockModel(vocab_size, index_of_edge, index_of_the, index_of_dog) # You can change these parameters as you wish.
mock_model.to(device)

mock_x_indexes = torch.tensor([
    [index_of_edge, index_of_dog, index_of_the, index_of_the],
    [index_of_edge, index_of_the, index_of_dog, index_of_dog],
], dtype=torch.int64, device=device)

mock_expected_logits = torch.zeros((2, 4, vocab_size), dtype=torch.float32, device=device)
mock_expected_logits[0, 0, index_of_the] = 2
mock_expected_logits[0, 1, index_of_the] = 2
mock_expected_logits[0, 2, index_of_dog] = 2
mock_expected_logits[0, 3, index_of_dog] = 2
mock_expected_logits[1, 0, index_of_the] = 2
mock_expected_logits[1, 1, index_of_dog] = 2
mock_expected_logits[1, 2, index_of_the] = 2
mock_expected_logits[1, 3, index_of_the] = 2

mock_logits = mock_model(mock_x_indexes)
assert mock_logits.shape == mock_expected_logits.shape, 'Output shape is invalid.'
assert mock_logits.dtype == mock_expected_logits.dtype, 'Output data type is invalid.'
assert np.unique(mock_logits.detach().cpu().numpy()).tolist() == [0.0, 2.0], 'Output has values other than 0 and 2'
assert (mock_logits == mock_expected_logits).all(), 'Output has the the wrong logits.'
print('\033[1m' + 'Correct!' + '\033[0m')

Correct!


2.2) Next, we need a function that measures the perplexity of a language model on the dev set.
Your function must take a model and a data set of token indexes and return the perplexity over the entire data set.

Hints:

* Don't forget that the perplexity includes the probability of the edge token at the end of the sentence.
* Don't forget to ignore pad tokens.

Use this function to find the mock model's perplexity on the dev set, which should be equal to `7062.2`.

In [22]:
def measure_perplexity(dataset, model, index_mapping):
    """Takes a dataset and a model and measures the perplexity of the language model on the dataset.
    
    Args:
        dataset (list): A list of sentences, where each sentence is a list of words.
        model: The language model.
        index_mapping (dict): A dictionary mapping tokens to indices.
        
    Returns:
        float: The perplexity of the language model on the dataset.
    """
    # Initializing perplexity
    perplexity = 0.0
    
    # Pad tokens will be ignored in the perplexity calculation
    pad_token = get_index(PADDING_TOKEN, index_mapping)
    
    # Calculating the perplexity, setting the model to not train
    with torch.no_grad():
        # Creating a tensor encompassing all the sentences in the dataset
        dataset_tensor = torch.tensor(
            [
            [get_index(token, index_mapping) for token in sentence] # Retrieving the index of each token in the sentence
            for sentence in dataset # Iterating through all of the sentences in the dataset
            ], 
            dtype=torch.int64, device=device)
        
        # Creating a tensor of the logits for the dataset
        dataset_logits = model(dataset_tensor)

        # Measuring the perplexity using binary cross entropy loss
        perplexity = torch.nn.functional.cross_entropy(dataset_logits.view(-1, dataset_logits.shape[-1]), 
                                                       dataset_tensor.view(-1), ignore_index=pad_token).exp().item()

    # Returning the perplexity
    return perplexity

In [23]:
perplexity = measure_perplexity(processed_dev_sentences, mock_model, index_mapping=index_mapping)
print('\033[1m' + 'The perplexity of the mock model on the dev set:' + '\033[0m' + ' {}'.format(perplexity))
# ----------------------- Wrong should be 7062.25 --------------------------------
# ----------------------- Need to do it via cross entropy loss -------------------

The perplexity of the mock model on the dev set: 7879.33056640625


## 3) Compression and decompression (20%)

We will now write the code that makes the actual compression and decompression of a text.

The compression algorithm will work as follows:

* You have a string of text to compress called `text` and a language model called `model`.
* Extract a list of tokens from `text` called `tokens` and a list of corresponding token indexes called `indexes`.
* Use `model` on `indexes` to produce `predicted`, a list of predicted next tokens for every index in `indexes`.
    A predicted next token is just the most probable token according to `model`.
* If a token in `predicted` corresponds to a token in `tokens`, then that token can be predicted by the model from its previous tokens.
    In this case, we don't need to have the token written down as it can be predicted, so we replace it in `tokens` with the single letter 'X' to say that a token should be predicted here.
    If 'X' is shorter than the replaced token, then the text will become shorter.
    Since all the text in our data sets is in lowercase, there will never be an 'X' in a sentence, so we can safely use it as a flag.
* If the token isn't correctly predicted then we leave the token in the text as-is.
* After all predictable tokens in `tokens` have been replaced with an 'X', return `tokens` as a space separated string.

The decompression algorithm will work as follows:

* You have a string of compressed text called `text` and a language model called `model`.
* Extract a list of tokens from `text` called `tokens`.
* Go through the tokens in `tokens` from the front and stop at the first 'X'.
* Convert all the tokens before the 'X' to token indexes called `indexes`.
* Use `model` to predict what the most probable token at the end of `indexes` would be.
* Replace the 'X' in `tokens` with this most probable token.
* Repeat this for every 'X'.
* After all 'X' are replaced in `tokens`, return `tokens` as a space separated string.

Do the following tasks:

3.1) Start with the compression function.
The input text will consist of sentences separated by new lines and space separated tokens (just like the raw data sets).
The function should return a single string with each line in the input text being compressed.
Remember that we want a compressed text to be decompressed back into the exact original text, which means that all out-of-vocabulary tokens must be left as-is (**there must not be any unknown tokens in the output**).

Print out the result of compressing this sentence using the mock model:

`the dog bit the cat sensually .`

which should be compressed into:

`X X bit X cat sensually .`

Hints:

* You don't need to follow the algorithm described above exactly (you can use different variable names and you can use new variables).
* Don't forget that out of vocabulary tokens still need to be replaced with the unknown token when creating the token indexes.
    What you can't do is return unknown tokens in the compressed output.
* The most probable token index for all token positions at once can be found from the logits by using `.argmax(1)`.
* Do not compare the token indexes of the uncompressed sentence to the predicted token indexes as otherwise the unknown token can be considered a correct prediction.
    Instead, compare the predictions with the string tokens in the uncompressed sentence.

In [24]:
def compress(text, model, index_mapping):
    """Compresses the given text using the given model.

    Note:
        The text is being split into sentences, so that the length of each sentence can be regularized to the 
        length of the largest sentence in the text. This is done to ensure that the model is fed a tensor of
        fixed size, and thus the model can be trained on a batch of tensors of the same size.

    Args:
        text (str): The text to compress, which consists of sentences separated by new lines and space separated tokens.
        model: The language model. 
        index_mapping (dict): A dictionary mapping tokens to indices. 

    Returns:
        str: The compressed text.
    """
    # Extracting a list of tokens for each sentence in the text, splitting by new lines first, then by spaces
    sentences = [sentence.split() for sentence in text.split('\n')]

    # Retrieving the maximum length of a sentence in the calculated sentences
    max_length = max([len(sentence) for sentence in sentences])

    # Creating a dictionary to store the index of each token
    indexes = {}
    # Iterating through the sentences and tokens, and adding the index of each token to the dictionary
    for sentence in sentences:
        for token in sentence:
            indexes[token] = get_index(token, index_mapping)

    # Creating a multi-sized tensor of the indexes of the tokens for each sentence,
    # and adding the edge token to the beginning, and appending padding tokens to the end depending on the maximum length
    x_indexes = torch.tensor(
        [
            [index_mapping.get(EDGE_TOKEN, -1)] +
            [indexes.get(token, -1) for token in sentence] +
            [index_mapping.get(PADDING_TOKEN, -1)] * (max_length - len(sentence))
            for sentence in sentences # Including all the above constructs in a list comprehension
        ],
        dtype=torch.int64,
        device=device
    )

    # Predicting the logits for the tokens to produce a tensor
    predicted = model(x_indexes)

    # Looping through the predicted logits, and for each sentence, predicting the next token
    for i in range(len(predicted)):
        # Predicting the next token for each token in the sentence
        predicted_tokens = torch.argmax(predicted[i], dim=1)

        # If the predicted token is the same as the original token, then set the original token to 'X'
        for j in range(len(sentences[i])):
            if predicted_tokens[j] == indexes[sentences[i][j]]:
                sentences[i][j] = 'X'  # Setting the token to 'X' as X is only 1 character long and thus space will be saved

    # Joining the tokens into a string and returning compressed text
    compressed_text = '\n'.join([' '.join(sentence) for sentence in sentences])
    return compressed_text

In [25]:
test_text = "the dog bit the cat sensually ."
compressed_text = compress(test_text, mock_model, index_mapping=index_mapping)

print('\033[1m' + 'Original text:' + '\033[0m' + ' {}'.format(test_text))
print('\033[1m' + 'Compressed text:' + '\033[0m' + ' {}'.format(compressed_text))

Original text: the dog bit the cat sensually .
Compressed text: X X bit X cat sensually .


3.2) Now write the decompression function.
Again, The input text will consist of sentences separated by new lines and space separated tokens, only this time, some of those tokens will be an 'X'.
The function should return a single big string where each line in the compressed text is decompressed back into the original input line.

Print out the result of decompressing the compressed text:

`X X bit X cat sensually .`

which should be decompressed into:

`the dog bit the cat sensually .`

Hints:

* You cannot use the language model once to predict all 'X's at once because the sentence prefix leading up to the 'X' must not have another 'X' in it.
    So you have to make a separate language model prediction for every 'X' using only the tokens that come before 'X' as input to the language model (plus the edge token at the front).
* Don't forget that the input to the language model cannot contain 'X's, so make sure that you're replacing those 'X's with their predicted token when constructing the language model input.


In [26]:
def decompress(text, model, index_mapping):
    """Decompresses the given text using the given model.

    Args:
        text (str): The text to decompress, which consists of sentences separated by new lines and space separated tokens.
        model: The language model. 
        index_mapping (dict): A dictionary mapping tokens to indices. 

    Returns:
        str: The decompressed text.
    """
    # Extracting a list of tokens for each sentence in the text, splitting by new lines first, then by spaces
    sentences = [sentence.split() for sentence in text.split('\n')]

    # Creating a dictionary to store the token of each index
    index2token = {index: token for token, index in index_mapping.items()}
    
    # Looping through all the sentences
    for sentence in sentences:
        # Looping through all the tokens, and once a token is 'X', convert the tokens to indices
        for token in sentence:
            if(token == 'X'):
                # Creating a tensor of the indexes of the tokens, adding the edge token to the beginning, and only taking the tokens before the 'X' token
                x_indexes = torch.tensor([get_index(EDGE_TOKEN,index_mapping)] + [get_index(token,index_mapping) for token in sentence[:sentence.index(token)]], dtype=torch.int64, device=device)
                
                # Predicting the logits for the tokens to produce a list
                predicted = model(x_indexes.unsqueeze(0))[0]

                # Retrieving the index of the token with the highest probability through the argmax function
                predicted = torch.argmax(predicted, dim=1)

                # Retrieving the token from the index
                new_token = index2token[predicted[-1].item()]
                
                # Replacing the 'X' token with the new token
                sentences[sentences.index(sentence)][sentence.index(token)] = new_token

    # Joining the tokens into a string and returning compressed text
    decompressed_text = '\n'.join([' '.join(sentence) for sentence in sentences])
    return decompressed_text

In [27]:
test_text = "X X bit X cat sensually ."
decompressed_text = decompress(test_text, mock_model, index_mapping=index_mapping)

print('\033[1m' + 'Compressed text:' + '\033[0m' + ' {}'.format(test_text))
print('\033[1m' + 'Decompressed text:' + '\033[0m' + ' {}'.format(decompressed_text))

Compressed text: X X bit X cat sensually .
Decompressed text: the dog bit the cat sensually .


3.3) Next, calculate and print the space saving amount of the mock model on the test set.
The space saving amount is calculated as follows:

$$\text{space\_saving}(t) = 1 - \frac{|\text{compress}(t)|}{|t|}$$

where $|t|$ is the number of characters in text $t$.

This measure tells you what fraction of the original size has been shaved off after compression (higher is better).
The mock model should give 2.4%.

In [28]:
def calculate_space_saving(text, model, index_mapping):
    """Calculates the space saving of the given text.
    
    Formula:
        Space_saving(text) = 1 - (length(compress(text)) / length(text))
        
    Args:
        text (str): The text to calculate the space saving of, which consists of sentences separated by new lines and space separated tokens.
        model: The language model. 
        index_mapping (dict): A dictionary mapping tokens to indices. 
        
    Returns:
        float: The percentage of the space saved by compressing the text.
    """
    # Calculating the length of the original text and the compressed text
    
    # Length of original text
    t = len(text) 

    # Length of compressed text
    c = len(compress(text, model, index_mapping=index_mapping)) 

    # Calculating space saved
    space_saved = 1 - (c/t) 

    # Multiplying result by 100 to get percentage
    return space_saved * 100 

In [29]:
# Calculating the space saved by the mock model on the test set mentioned above
space_saved = calculate_space_saving(test_set, mock_model, index_mapping=index_mapping)

# Rounding the space saved to 2 decimal places
print('\033[1m' + 'The space saving of the mock model on the test set:' + '\033[0m' + ' {}%'.format(round(space_saved, 1)))

The space saving of the mock model on the test set: 2.4%


## 4) Making and using a language model (50%)

Now we finally train a language model and use it to compress the test set.

Do the following tasks:

4.1) Train a neural language model on the train set.
After training, show a graph of how the *dev set perplexity* varies with each epoch (use the perplexity function you wrote above).

In [30]:
# class NeuralLanguageModel(torch.nn.Module):
#     """Neural language model which can be used to compress text."""
    
#     def __init__(self, vocab_size):
#         super().__init__()
#         self.vocab_size = vocab_size
        
#     def forward(self, x_indexes):


4.2) Now measure the space saving amount of the trained model on the test text.
Also check that when you decompress the compressed test text, you get exactly the same string as the test text.

Note: You may need to strip off the new line character from the end of the test text when comparing it to the decompressed text.

4.3) Now you need to analyse the model's output.
Split the test text into sentences and compress each individual sentence.
Print out the top 5 most compressed sentences and the top 5 least compressed sentences according to the space saving metric together with the compressed sentences.

4.4) Is the reason for whether a sentence is compressible or not due to its similarity to the train set (a sentence that is similar to one in the train set would be easier to predict and thus more tokens will be compressed)?
Find out the answer to this by doing the following:

Extract all the trigrams from the train set (you can use `nltk.trigrams` to do this).
For each sentence in the test set, count how many of its trigrams are also found in the train set.
Turn this count into a domain similarity measure by dividing it by the number of trigrams in the test sentence.

Note: In order for this fraction to be meaningful from the language model's point of view, the edge token must be added to the front of the test sentences and out-of-vocabulary tokens must be replaced with the unknown token.

Create a list that maps each sentence's domain similarity to its space saving amount.
Plot a scatter plot showing how the domain similarity measure relates to the space saving amount of each test sentence.
If there is a correlation between these two measures, then the points in the scatter plot will form approximately into a straight line.

4.5) The scatter plot should not have created a straight line and should show a lot of bias towards very low space saving amounts, regardless of domain similarity.
Why is domain similarity not enough for explaining the compressability?

## 5) Conclusions (10%)

Write the following conclusions:

5.1) What is a simple change in the compression algorithm that can be made to increase compression?
Do not suggest any fundamental changes; the algorithm must still work by predicting missing tokens.

5.2) Write, in less than 300 words, your interpretation of the results and how you think the model could perform better.
You should talk about things like overfitting/underfitting and whether the model is learning anything deep about English sentences.